In [69]:
# Generating Shakespeare Text Using a Character RNN

import numpy as np
import tensorflow as tf
from tensorflow import keras

# step 1: load the data
shakespeare_url = "https://homl.info/shakespeare" # shortcut URL
filepath = keras.utils.get_file("shakespeare.txt", shakespeare_url)
with open(filepath) as f:
    shakespeare_text = f.read()

# step 2: tokenization
tokenizer = keras.preprocessing.text.Tokenizer(char_level=True)
#tokenizer.fit_on_texts(shakespeare_text) old line with text input as a list.
tokenizer.fit_on_texts(shakespeare_text)

In [70]:
# step 3: try to create a training dataset
max_id = len(tokenizer.word_index) # number of distinct characters
dataset_size = tokenizer.document_count # total number of characters
print(max_id, dataset_size)

39 1115394


In [71]:
[encoded] = np.array(tokenizer.texts_to_sequences([shakespeare_text])) - 1
train_size = dataset_size * 90 // 100
dataset = tf.data.Dataset.from_tensor_slices(encoded[:train_size])

# step 4: chopping the sequential dataset into multiple windows
# we will use the dataset's window() method to convert this long sequence of characters into many
# smaller windows of text.

n_steps = 100
window_length = n_steps + 1 # target = input shifted 1 character ahead
dataset = dataset.window(window_length, shift=1, drop_remainder=True)

dataset = dataset.flat_map(lambda window: window.batch(window_length))

batch_size = 32
dataset = dataset.shuffle(10000).batch(batch_size)
dataset = dataset.map(lambda windows: (windows[:, :-1], windows[:, 1:]))

dataset = dataset.map(
    lambda X_batch, Y_batch: (tf.one_hot(X_batch, depth=max_id), Y_batch))
dataset = dataset.prefetch(1)

In [73]:
# step 5: build the model (RNN with 2 GRU layers of 128 units each, and 20% dropout on both
# inputs (drop_out) and the hidden states (recurrent_dropout).
model = keras.models.Sequential([
    keras.layers.GRU(128, return_sequences=True, input_shape=[None, max_id],
                     dropout=0.2, recurrent_dropout=0.2),
    keras.layers.GRU(128, return_sequences=True,
                     dropout=0.2, recurrent_dropout=0.2),
    keras.layers.TimeDistributed(keras.layers.Dense(max_id,
                                                    activation="softmax"))
])
model.compile(loss="sparse_categorical_crossentropy", optimizer="adam")

# since it is a demo, I just train 1 epoch
history = model.fit(dataset,steps_per_epoch=train_size // batch_size, epochs=1)

31370/31370 [==============================] - 8161s 260ms/step - loss: 1.5920


In [74]:
# now we have a model that can predict the next character in text written by Shakespeare.

def preprocess(texts):
    X = np.array(tokenizer.texts_to_sequences(texts)) - 1
    return tf.one_hot(X, max_id)

# now lets use the model to predict the next letter in some text:
# Keep in mind that the model only trained one epoch. the loss is still high.
# this is just a demo

X_new = preprocess(["How are yo"])
Y_pred = model.predict_classes(X_new)
tokenizer.sequences_to_texts(Y_pred + 1)[0][-1]

# You can see, the last character is 'u'

/Users/rwang/my_env/lib/python3.7/site-packages/tensorflow/python/keras/engine/sequential.py:450: UserWarning: `model.predict_classes()` is deprecated and will be removed after 2021-01-01. Please use instead:* `np.argmax(model.predict(x), axis=-1)`,   if your model does multi-class classification   (e.g. if it uses a `softmax` last-layer activation).* `(model.predict(x) > 0.5).astype("int32")`,   if your model does binary classification   (e.g. if it uses a `sigmoid` last-layer activation).
  warnings.warn('`model.predict_classes()` is deprecated and '


'u'

In [78]:
# Now let's use this model to generate fake Shakespearean Text
def next_char(text, temperature=1):
    X_new = preprocess([text])
    y_proba = model.predict(X_new)[0, -1:, :]
    rescaled_logits = tf.math.log(y_proba) / temperature
    char_id = tf.random.categorical(rescaled_logits, num_samples=1) + 1
    return tokenizer.sequences_to_texts(char_id.numpy())[0]

def complete_text(text, n_chars=50, temperature=1):
    for _ in range(n_chars):
        text += next_char(text, temperature)
    return text


print(complete_text("t", temperature=1))
print(complete_text("w", temperature=1))

# Apparently our Shakespeare model works not well, caz our training model did not converge.

t'd fancy
as more than do in the rass to such a
sco
will prove, sir, when i praw her, dancy in perfumes
